In [1]:
%load_ext autoreload

%autoreload 2

In [2]:
from statsmodels.sandbox.stats.multicomp import multipletests

from environment import *
from analysis import *

CCAL version 0.6.25 @ /home/kwatme/miniconda3/lib/python3.6/site-packages/ccal/__init__.py


In [3]:
np.random.seed(20121020)

In [4]:
feature_x_sample = pd.read_table(
    '../output/max_tpm__gene_x_sample.tsv',
    index_col=0,
)

In [5]:
target_x_sample = pd.read_table(
    '../data/target_x_sample.tsv',
    index_col=0,
)

target_x_sample

NC1_tpm  NC2_tpm  NC3_tpm  NM1_tpm  NM2_tpm  NM3_tpm  WC1_tpm  \
NC vs NM        0        0        0        1        1        1       -1   
WC vs WM       -1       -1       -1       -1       -1       -1        0   

          WC2_tpm  WC3_tpm  WM1_tpm  WM2_tpm  WM3_tpm  
NC vs NM       -1       -1       -1       -1       -1  
WC vs WM        0        0        1        1        1

In [6]:
n_permutation = 300

for target_x_sample__index, target in target_x_sample.iterrows():
    
    target = target[target!=-1]
    
    feature_x_sample_ = feature_x_sample[target.index]
    
    feature_x_target = feature_x_sample_.groupby(
        by=target,
        axis=1,
    ).mean()
    
    feature_score = ccal.compute_log_ratio_between_2_1d_arrays(
        feature_x_target.iloc[:, 0] + 1, 
        feature_x_target.iloc[:, 1] + 1,
        log_base='2',
    ) 
    
    feature_x_permutation = np.full(
        (
            feature_x_sample.shape[0],
            n_permutation,
        ),
        np.nan,
    )

    for i in range(n_permutation):

        np.random.shuffle(target)

        feature_x_target = feature_x_sample_.groupby(
            by=target,
            axis=1,
        ).mean()

        feature_x_permutation[:, i] = ccal.compute_log_ratio_between_2_1d_arrays(
            feature_x_target.iloc[:, 0] + 1, 
            feature_x_target.iloc[:, 1] + 1,
            log_base='2',
        ) 

    p_values = np.full(
        feature_score.size,
        np.nan,
    )

    for i, score in enumerate(feature_score):

        random_scores = feature_x_permutation[i]

        p_values[i] = min(
            ccal.compute_empirical_p_value(
                score,
                random_scores,
                'less'
            ),
            ccal.compute_empirical_p_value(
                score,
                random_scores,
                'great'
            ),
        )

    feature_p_value = pd.Series(
        p_values,
        index=feature_score.index,
    )


    feature_score_p_value_fdr = pd.concat(
        (
            feature_score,
            feature_p_value,
            pd.Series(
                multipletests(
                    feature_p_value,
                    method='fdr_bh',
                )[1],
                index=feature_p_value.index,
            ),
        ),
        axis=1,
    )

    feature_score_p_value_fdr.columns = (
        'Score',
        'P-Value',
        'FDR',
    )

    feature_score_p_value_fdr.sort_values(
        'P-Value',
        inplace=True,
    )

    print(feature_score_p_value_fdr.head(n=32))
    
    feature_score_p_value_fdr.to_csv(
        '../output/gene/{} Fold Change.tsv'.format(target_x_sample__index),
        sep='\t',
    )

    scores_0 = feature_score_p_value_fdr['Score']

    scores_1 = pd.read_table(
        '../output/gene/{}.tsv'.format(target_x_sample__index),
        index_col=0,
    )['Score']

    scores_0 = scores_0[scores_0.index & scores_1.index].sort_values()

    scores_1 = scores_1[scores_0.index]

    ccal.plot_points(
        ('Scores', ),
        (scores_0, ),
        (scores_1, ),
        texts=(scores_0.index, ),
    )

              Score   P-Value      FDR
MED7      -0.457028  0.066667  0.20739
PLEKHJ1   -0.270250  0.066667  0.20739
PLEKHF1   -0.178604  0.066667  0.20739
PLEKHA8P1  0.546772  0.066667  0.20739
ENDOV     -0.459251  0.066667  0.20739
PLEKHA3    0.572794  0.066667  0.20739
PLD3      -0.384804  0.066667  0.20739
PLCB4      0.275998  0.066667  0.20739
ENHO      -0.290297  0.066667  0.20739
ENO2       0.393234  0.066667  0.20739
PLAC8      0.223104  0.066667  0.20739
ENPEP      0.293361  0.066667  0.20739
PLA2G4F    0.106190  0.066667  0.20739
PLA2G4E    0.132220  0.066667  0.20739
PLA2G12A   0.434712  0.066667  0.20739
ENTPD3     0.143892  0.066667  0.20739
PKNOX2     0.085238  0.066667  0.20739
PKNOX1     0.403467  0.066667  0.20739
PLG        0.134862  0.066667  0.20739
PLGLB1     0.371129  0.066667  0.20739
EMSY       0.912192  0.066667  0.20739
PLK2       0.994820  0.066667  0.20739
EIF4EBP3  -0.741428  0.066667  0.20739
POFUT1     0.532632  0.066667  0.20739
ELF1       0.412669  0.06

           Score   P-Value      FDR
SFT2D2 -0.906024  0.033333  0.11164
WAPL   -0.557532  0.033333  0.11164
KRT27  -0.105161  0.033333  0.11164
ARPC5L -0.553704  0.033333  0.11164
ARPIN  -0.936495  0.033333  0.11164
ARPP19 -0.489622  0.033333  0.11164
TEX2   -0.815982  0.033333  0.11164
ARR3   -0.227175  0.033333  0.11164
ARRB1  -0.445583  0.033333  0.11164
WARS   -0.374089  0.033333  0.11164
ARRDC1 -0.491563  0.033333  0.11164
ARRDC3 -1.385169  0.033333  0.11164
KRT23  -0.162148  0.033333  0.11164
VWF    -0.148152  0.033333  0.11164
ARSB   -0.666596  0.033333  0.11164
TEX21P -0.474963  0.033333  0.11164
KRT20  -0.064514  0.033333  0.11164
ARSG   -0.506013  0.033333  0.11164
ARSI   -1.479584  0.033333  0.11164
ARRDC2 -0.807334  0.033333  0.11164
KRT31  -0.113054  0.033333  0.11164
ARPC3   0.212274  0.033333  0.11164
KRT32  -0.334840  0.033333  0.11164
KRT75  -0.527714  0.033333  0.11164
KRT74  -0.042597  0.033333  0.11164
TET3   -1.492392  0.033333  0.11164
ARMC12 -0.072055  0.033333  